## Import Libraries

In [23]:
import pandas as pd
import numpy as np
import torch
import torchvision.transforms as transforms
import os
from PIL import Image

## Convert to Low Light

In [24]:
class MAETLowLightTransform:
    def __init__(self, alpha=0.3, beta=0.8, noise_level=0.02, device="cpu"):
        """
        Initialize the transformation with specific parameters.
        
        Args:
        - alpha: Exposure degradation factor (lower = darker)
        - beta: Gamma correction factor
        - noise_level: Amount of noise to add
        - device: "cuda" or "cpu" for PyTorch tensor computations
        """
        self.alpha = alpha
        self.beta = beta
        self.noise_level = noise_level
        self.device = device

    def apply_transform(self, image_tensor):
        """
        Apply the physics-based low-light degradation on an image tensor.

        Args:
        - image_tensor: A PyTorch tensor of shape (C, H, W), range [0, 1]
        
        Returns:
        - Transformed low-light image tensor
        """
        # Ensure image is on the correct device
        image_tensor = image_tensor.to(self.device)

        # Step 1: Reduce brightness (Exposure degradation)
        low_light_img = image_tensor * self.alpha

        # Step 2: Apply gamma correction (non-linear transformation)
        low_light_img = torch.pow(low_light_img, self.beta)

        # Step 3: Add Gaussian noise
        noise = torch.randn_like(low_light_img) * self.noise_level
        low_light_img = torch.clamp(low_light_img + noise, 0, 1)

        return low_light_img

# Load and preprocess an image
def load_image(image_path, device="cpu"):
    transform = transforms.Compose([
        transforms.ToTensor()  # Converts to (C, H, W) format with range [0, 1]
    ])
    image = Image.open(image_path).convert("RGB")
    return transform(image).to(device)

# Convert tensor back to image and save
def save_image(tensor, output_path):
    transform = transforms.ToPILImage()
    image = transform(tensor.cpu())  # Convert to PIL image
    os.makedirs(os.path.dirname(output_path), exist_ok=True)  # Ensure output directory exists
    image.save(output_path)

# Process all images in a folder recursively while maintaining directory structure
def process_folder(device="cpu"):
    # Initialize the MAET transformation
    maet = MAETLowLightTransform(device=device)

    input_path = os.getcwd().replace('notebook' , '') + 'dataset'
    os.mkdir(os.getcwd().replace('notebook' , '') + 'output_dataset') if 'output_dataset' not in os.listdir(os.getcwd().replace('notebook' , '')) else None
    output_path = os.getcwd().replace('notebook' , '') + 'output_dataset'
    
    # Walk through the directory
    for folder in os.listdir(input_path):
        if folder != '.DS_Store':
            os.mkdir(output_path + '/' + folder) if folder not in os.listdir(output_path) else None
            for file in os.listdir(input_path + '/' + folder):
                if file.lower().endswith((".png", ".jpg", ".jpeg", ".bmp", ".tiff")):  # Supported formats
                    input_file_path = input_path + '/' +  folder + '/' + file
                    
                    # Create corresponding output path
                    output_file_path = output_path + '/' + folder + '/' + file

                    print(f"Processing: {input_file_path} -> {output_file_path}")

                    # Load image
                    image_tensor = load_image(input_file_path, device)

                    # Apply low-light transformation
                    low_light_tensor = maet.apply_transform(image_tensor)

                    # Save output image
                    save_image(low_light_tensor, output_file_path.replace(" " , "_"))

# Example usage
if __name__ == "__main__":
    device = "cuda" if torch.cuda.is_available() else "cpu"

    print(f"Processing images using {device.upper()}...")
    process_folder(device)
    print("Processing complete!")


Processing images using CPU...
Processing: /Users/pranitdas/Desktop/Agriculture_quantum_image_classifcation/dataset/Tomato_healthy/9e2a71e5-2a59-4e62-9c6c-581fe9091a10___RS_HL 0132.JPG -> /Users/pranitdas/Desktop/Agriculture_quantum_image_classifcation/output_dataset/Tomato_healthy/9e2a71e5-2a59-4e62-9c6c-581fe9091a10___RS_HL 0132.JPG
Processing: /Users/pranitdas/Desktop/Agriculture_quantum_image_classifcation/dataset/Tomato_healthy/e2991a66-412d-4841-8dc0-524e38338a82___GH_HL Leaf 517.1.JPG -> /Users/pranitdas/Desktop/Agriculture_quantum_image_classifcation/output_dataset/Tomato_healthy/e2991a66-412d-4841-8dc0-524e38338a82___GH_HL Leaf 517.1.JPG
Processing: /Users/pranitdas/Desktop/Agriculture_quantum_image_classifcation/dataset/Tomato_healthy/a5e54e01-2cd5-482a-bfba-8728ca32473c___GH_HL Leaf 426.JPG -> /Users/pranitdas/Desktop/Agriculture_quantum_image_classifcation/output_dataset/Tomato_healthy/a5e54e01-2cd5-482a-bfba-8728ca32473c___GH_HL Leaf 426.JPG
Processing: /Users/pranitdas/De